# Pre-processing procedure for 2018 n2c2 dataset

## functions 

In [1]:
from pathlib import Path
import pickle as pkl
from collections import defaultdict, Counter
from itertools import permutations, combinations
from functools import reduce
import numpy as np
import os

In [2]:
def pkl_save(data, file):
    with open(file, "wb") as f:
        pkl.dump(data, f)
        
def pkl_load(file):
    with open(file, "rb") as f:
        data = pkl.load(f)
    return data

def load_text(ifn):
    with open(ifn, "r") as f:
        txt = f.read()
    return txt

In [3]:
import sys
sys.path.append("/home/zehao.yu/workspace/py3/NLPreprocessing")
from annotation2BIO import pre_processing, read_annotation_brat, generate_BIO
MIMICIII_PATTERN = "\[\*\*|\*\*\]"

In [4]:
def create_entity_to_sent_mapping(nnsents, entities, idx2e):
    loc_ens = []
    
    ll = len(nnsents)
    mapping = defaultdict(list)
    for idx, each in enumerate(entities):
        en_label = idx2e[idx]
        en_s = each[2][0]
        en_e = each[2][1]
        new_en = []
        
        i = 0
        while i < ll and nnsents[i][1][0] < en_s:
            i += 1
        s_s = nnsents[i][1][0]
        s_e = nnsents[i][1][1]

        if en_s == s_s:
            mapping[en_label].append(i)

            while i < ll and s_e < en_e:
                i += 1
                s_e = nnsents[i][1][1]
            if s_e == en_e:
                 mapping[en_label].append(i)
            else:
                mapping[en_label].append(i)
                print("last index not match ", each)
        else:
            mapping[en_label].append(i)
            print("first index not match ", each)

            while i < ll and s_e < en_e:
                i += 1
                s_e = nnsents[i][1][1]
            if s_e == en_e:
                 mapping[en_label].append(i)
            else:
                mapping[en_label].append(i)
                print("last index not match ", each)
    return mapping


def get_permutated_relation_pairs(eid2idx):
    all_pairs = []
    all_ids = [k for k, v in eid2idx.items()]
    for e1, e2 in permutations(all_ids, 2):
        all_pairs.append((e1, e2))
    return all_pairs

In [5]:
"""
procedure:

1. preprocess text into sentences
2. find each entity associated sentence idx
3. generate entity pairs as relation candidates
4. extract eneity associated sentences, locate entities in pair and insert special tags
5. save generated data

result output:

1. keep pos predicted relations
2. using map files to locate relation associated entities
3. output as brat
"""
def validate_rels(rels, valid):
    nrels = []
    for rel in rels:
        rtype = rel[0]
        if tuple(rtype) not in valid:
            print("invalid: ", rel)
            continue
        nrels.append(rel)
    return nrels


def check_tags(s1, s2):
    assert EN1_START in s1 and EN1_END in s1, f"tag error: {s1}"
    assert EN2_START in s2 and EN2_END in s2, f"tag error: {s2}"


def format_relen(en, rloc, nsents):
    if rloc == 1:
        spec1, spec2 = EN1_START, EN1_END
    else:
        spec1, spec2 = EN2_START, EN2_END
    sn1, tn1 = en[0][3]
    sn2, tn2 = en[-1][3]
    target_sent = nsents[sn1]
    target_sent = [each[0] for each in target_sent]
    ors =  " ".join(target_sent)
    
    if sn1 != sn2:
#         print("[!!!Warning] The entity is not in the same sentence\n", en)
        tt = nsents[sn2]
        tt = [each[0] for each in tt]
        target_sent.insert(tn1, spec1)
        tt.insert(tn2+1, spec2)
        target_sent = target_sent + tt
#         print(target_sent)
    else:
        target_sent.insert(tn1, spec1)
        target_sent.insert(tn2+2, spec2)
    
    fs = " ".join(target_sent)
    
    return sn1, sn2, fs, ors


def gene_true_relations(rels, mappings, ens, e2i, nnsents, nsents, valid_comb, fid=None):
    true_pairs = set()
    pos_samples = []
    
    for rel in rels:
        rel_type = rel[0]
        enid1, enid2 = rel[1:]
        """
        [['100', (15443, 15446), (16473, 16476), (231, 4), 'B-Strength'], 
        ['mg', (15447, 15449), (16477, 16479), (231, 5), 'I-Strength']] 
        [['Metoprolol', (15422, 15432), (16452, 16462), (231, 2), 'B-Drug'], 
        ['Succinate', (15433, 15442), (16463, 16472), (231, 3), 'I-Drug']]
        """
        enbs1, enbe1 = mappings[enid1]
        en1 = nnsents[enbs1: enbe1+1]
        si1, sii1, fs1, ors1 = format_relen(en1, 1, nsents)
        enbs2, enbe2 = mappings[enid2]
        en2 = nnsents[enbs2: enbe2+1]
        si2, sii2, fs2, ors2 = format_relen(en2, 2, nsents)
        sent_diff = abs(si1 - si2)
        
        en1t = en1[0][-1].split("-")[-1]
        en2t = en2[0][-1].split("-")[-1]

        true_pairs.add((enid1, enid2))
        
        if (en1t, en2t) not in valid_comb:
            continue
        
        if sent_diff <= CUTOFF:
            check_tags(fs1, fs2)
            assert (en1t, en2t) in valid_comb, f"{en1t} {en2t}"
            if DO_BIN:
                pos_samples.append((sent_diff, "pos", fs1, fs2, en1t, en2t, enid1, enid2, fid))
            else:
                pos_samples.append((sent_diff, rel_type, fs1, fs2, en1t, en2t, enid1, enid2, fid))

    return pos_samples, true_pairs
        

def gene_neg_relation(perm_pairs, true_pairs, mappings, ens, e2i, nnsents, nsents, valid_comb, fid=None):
    neg_samples = []
    for each in perm_pairs:
        enid1, enid2 = each
        
        # not in true relation
        if (enid1, enid2) in true_pairs:
            continue
        
        enc1 = ens[e2i[enid1]]
        enc2 = ens[e2i[enid2]]

        enbs1, enbe1 = mappings[enid1]
        en1 = nnsents[enbs1: enbe1+1]
        si1, sii1, fs1, ors1 = format_relen(en1, 1, nsents)
        enbs2, enbe2 = mappings[enid2]
        en2 = nnsents[enbs2: enbe2+1]
        si2, sii2, fs2, ors2 = format_relen(en2, 2, nsents)
        sent_diff = abs(si1 - si2)
        
        en1t = en1[0][-1].split("-")[-1]
        en2t = en2[0][-1].split("-")[-1]
        
        if (en1t, en2t) not in valid_comb:
            continue
        
        if sent_diff <= CUTOFF:
            check_tags(fs1, fs2)
            assert (en1t, en2t) in valid_comb, f"{en1t} {en2t}"
            if fid:
                neg_samples.append((sent_diff, NEG_REL, fs1, fs2, en1t, en2t, enid1, enid2, fid))
            else:
                neg_samples.append((sent_diff, NEG_REL, fs1, fs2, en1t, en2t, enid1, enid2))
    
    return neg_samples

    
def create_training_samples(file_path, valids=None, valid_comb=None):
    fids = []
    root = Path(file_path)
    
    dpos = defaultdict(list)
    dneg = defaultdict(list)
    
    for txt_fn in root.glob("*.txt"):
        fids.append(txt_fn.stem)
        ann_fn = root / (txt_fn.stem+".ann")

        # load text
        txt = load_text(txt_fn)
        pre_txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
        e2i, ens, rels = read_annotation_brat(ann_fn)
        i2e = {v: k for k, v in e2i.items()}
        
        nsents, sent_bound = generate_BIO(sents, ens, file_id="", no_overlap=False, record_pos=True)
        print(nsents)
        total_len = len(nsents)
        nnsents = [w for sent in nsents for w in sent]
        mappings = create_entity_to_sent_mapping(nnsents, ens, i2e)

        pos_samples, true_pairs = gene_true_relations(
            rels, mappings, ens, e2i, nnsents, nsents, valid_comb, fid=txt_fn.stem)
        perm_pairs = get_permutated_relation_pairs(e2i)
        neg_samples = gene_neg_relation(
            perm_pairs, true_pairs, mappings, ens, e2i, nnsents, nsents, valid_comb, fid=txt_fn.stem)
        
        for pos_sample in pos_samples:
            dpos[pos_sample[0]].append(pos_sample)
        for neg_sample in neg_samples:
            dneg[neg_sample[0]].append(neg_sample)
        
    return dpos, dneg


def create_test_samples(file_path, valids=None, valid_comb=None):
    #create a separate mapping file
    rel_mappings = []
    #
    fids = []
    root = Path(file_path)
    preds = defaultdict(list)
    
    for txt_fn in root.glob("*.txt"):
        fids.append(txt_fn.stem)
        ann_fn = root / (txt_fn.stem + ".ann")

        # load text
        txt = load_text(txt_fn)
        pre_txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
        e2i, ens, _ = read_annotation_brat(ann_fn)
        i2e = {v: k for k, v in e2i.items()}
        
        nsents, sent_bound = generate_BIO(sents, ens, file_id="", no_overlap=False, record_pos=True)
        total_len = len(nsents)
        nnsents = [w for sent in nsents for w in sent]
        mappings = create_entity_to_sent_mapping(nnsents, ens, i2e)
        
        perm_pairs = get_permutated_relation_pairs(e2i)
        pred = gene_neg_relation(perm_pairs, set(), mappings, ens, e2i, nnsents, nsents, valid_comb, fid=txt_fn.stem)
        for idx, pred_s in enumerate(pred):
            preds[pred_s[0]].append(pred_s)
            
    return preds

In [6]:
"""
Output strategy:

1. by cross-distance
- no cross distance; all in one
- by cross distance; all in unique
- by partial cross distance; within-sentence vs. cross sentence

2. relation format
- [CLS] S1 [SEP] S2 [SEP]
- [CLS] S1 S2 [SEP]

We only handle (1) in data generation here, (2) will be handled by the data_utils
"""
def to_tsv(data, fn):
    header = "\t".join([str(i+1) for i in range(len(data[0]))])
    with open(fn, "w") as f:
        f.write(f"{header}\n")
        for each in data:
            d = "\t".join([str(e) for e in each])
            f.write(f"{d}\n")


def to_5_cv(data, ofd):
    if not os.path.isdir(ofd):
        os.mkdir(ofd)
    
    np.random.seed(13)
    np.random.shuffle(data)
    
    dfs = np.array_split(data, 5)
    a = [0,1,2,3,4]
    for each in combinations(a, 4):
        b = list(set(a) - set(each))[0]
        n = dfs[b]
        m = []
        for k in each:
            m.extend(dfs[k])
        if not os.path.isdir(os.path.join(ofd, f"sample{b}")):
            os.mkdir(os.path.join(ofd, f"sample{b}"))
        
        to_tsv(m, os.path.join(ofd, f"sample{b}", "train.tsv"))
        to_tsv(n, os.path.join(ofd, f"sample{b}", "dev.tsv"))


def all_in_one(*dd, dn="2018n2c2", do_train=True):
    data = []
    for d in dd:
        for k, v in d.items():
            for each in v:
                data.append(each[1:])
    
    output_path = f"/home/zehao.yu/workspace/py3/dr_ann/data/{dn}_aio_th{CUTOFF}"
    p = Path(output_path)
    p.mkdir(parents=True, exist_ok=True)
    
    if do_train:
        to_tsv(data, p/"train.tsv")
        if OUTPUT_CV:
            to_5_cv(data, p.as_posix())
    else:
        to_tsv(data, p/"test.tsv")
    

def all_in_unique(*dd, dn="2018n2c2", do_train=True):
    for idx in range(CUTOFF+1):
        data = []
        for d in dd:
            for k, v in d.items():
                for each in v:
                    if k == idx:
                        data.append(each[1:])
        
        output_path = f"/home/zehao.yu/workspace/py3/dr_ann/data/{dn}_aiu_th{CUTOFF}"
        p = Path(output_path) / f"cutoff_{idx}"
        p.mkdir(parents=True, exist_ok=True)
        if do_train:
            to_tsv(data, p/"train.tsv")
            if OUTPUT_CV:
                to_5_cv(data, p.as_posix())
        else:
            to_tsv(data, p/"test.tsv")

## GLOBAL CONFIG VARIABLES

In [7]:
# general pre-defined special tags
EN1_START = "[s1]"
EN1_END = "[e1]"
EN2_START = "[s2]"
EN2_END = "[e2]"
NEG_REL = "NonRel"
# max valid cross sentence distance
CUTOFF = 1
# output 5-fold cross validation data
OUTPUT_CV = False
# do binary classification (if false, then we do multiclass classification)
DO_BIN = False

In [10]:
train_dev_root ='/home/zehao.yu/workspace/py3/dr_ann/data/used/train_set'
test_root = '/home/zehao.yu/workspace/py3/dr_ann/data/used/test_set'
test_root_e2e='/home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/'

In [9]:
dr_valid_comb_en = {
    ('lesion', 'eye_part'), ('laterality', 'lesion'), ('severity', 'lesion')
}
entp2rel = {
    ('lesion', 'eye_part'):'located', 
    ('laterality', 'lesion'):'laterality-lesion', 
    ('severity', 'lesion'):'severity-lesion'
}

## Generate training data

In [13]:
dpos, dneg = create_training_samples(train_dev_root, None, dr_valid_comb_en)

2021-06-30 02:22:44,291 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,292 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,293 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_9152.txt ...
2021-06-30 02:22:44,360 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,361 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,361 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_863.txt ...
2021-06-30 02:22:44,419 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,420 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,421 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_4550.txt ...
2021-06-30 02:22:44,425 INFO ODOSMedications
2021-06-30 02:22:44,425 WARNING 'ODOSMedications' => 'ODOS' 'Medications'
2021-06-30 02:22:44,485 INFO sentenc

[[['Assessment', (0, 10), (0, 10), (0, 0), 'O'], ['and', (11, 14), (11, 14), (0, 1), 'O'], ['Plan', (15, 19), (15, 19), (0, 2), 'O'], [':', (19, 20), (20, 21), (0, 3), 'O'], ['ICD', (25, 28), (22, 25), (0, 4), 'O'], ['-', (28, 29), (26, 27), (0, 5), 'O'], ['10', (29, 31), (28, 30), (0, 6), 'O'], ['-', (31, 32), (31, 32), (0, 7), 'O'], ['CM', (32, 34), (33, 35), (0, 8), 'O'], ['ICD', (35, 38), (36, 39), (0, 9), 'O'], ['-', (38, 39), (40, 41), (0, 10), 'O'], ['9', (39, 40), (42, 43), (0, 11), 'O'], ['-', (40, 41), (44, 45), (0, 12), 'O'], ['CM', (41, 43), (46, 48), (0, 13), 'O'], ['1', (46, 47), (49, 50), (0, 14), 'O'], ['.', (47, 48), (51, 52), (0, 15), 'O']], [['Proliferative', (49, 62), (53, 66), (1, 0), 'B-lesion'], ['diabetic', (63, 71), (67, 75), (1, 1), 'I-lesion'], ['retinopathy', (72, 83), (76, 87), (1, 2), 'I-lesion'], ['of', (84, 86), (88, 90), (1, 3), 'O'], ['right', (87, 92), (91, 96), (1, 4), 'B-laterality'], ['eye', (93, 96), (97, 100), (1, 5), 'I-laterality'], ['with', (9

2021-06-30 02:22:44,545 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,546 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,547 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/1458921_note_3276.txt ...
2021-06-30 02:22:44,555 INFO DULoxetine
2021-06-30 02:22:44,556 WARNING 'DULoxetine' => 'DU' 'Loxetine'
2021-06-30 02:22:44,556 INFO LORazepam
2021-06-30 02:22:44,557 WARNING 'LORazepam' => 'LO' 'Razepam'
2021-06-30 02:22:44,629 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,630 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,630 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_6884.txt ...
2021-06-30 02:22:44,701 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,701 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,702 INFO current processing /home/zehao.yu/

[[['Visit', (0, 5), (0, 5), (0, 0), 'O'], ['Date', (6, 10), (6, 10), (0, 1), 'O'], [':', (10, 11), (11, 12), (0, 2), 'O'], ['DATE', (16, 20), (13, 17), (0, 3), 'O'], ['Referring', (26, 35), (18, 27), (0, 4), 'O'], ['Physician', (36, 45), (28, 37), (0, 5), 'O'], [':', (45, 46), (38, 39), (0, 6), 'O'], ['Dr.', (48, 51), (40, 43), (0, 7), 'O'], ['NAME', (55, 59), (45, 49), (0, 8), 'O'], ['Subjective', (63, 73), (50, 60), (0, 9), 'O'], ['Subjective', (75, 85), (61, 71), (0, 10), 'O'], [':', (85, 86), (72, 73), (0, 11), 'O'], ['Chief', (89, 94), (74, 79), (0, 12), 'O'], ['Complaint', (95, 104), (80, 89), (0, 13), 'O'], ['Patient', (106, 113), (90, 97), (0, 14), 'O'], ['presents', (114, 122), (98, 106), (0, 15), 'O'], ['with', (123, 127), (107, 111), (0, 16), 'O'], ['•', (129, 130), (112, 113), (0, 17), 'O'], ['Loss', (131, 135), (114, 118), (0, 18), 'O'], ['of', (136, 138), (119, 121), (0, 19), 'O'], ['Vision', (139, 145), (122, 128), (0, 20), 'O'], ['•', (147, 148), (129, 130), (0, 21), 'O

2021-06-30 02:22:44,824 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,827 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,827 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2260561_note_6253.txt ...
2021-06-30 02:22:44,912 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,912 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,913 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_6174.txt ...
2021-06-30 02:22:44,973 INFO sentence boundary detection class initiated.
2021-06-30 02:22:44,974 INFO word level tokenization with replace_number set to False
2021-06-30 02:22:44,974 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2698404_note_9114.txt ...
2021-06-30 02:22:45,036 INFO sentence boundary detection class initiated.
2021-06-30 02:22:45,037 INFO word level tokenization with replac

...

[[['OPH', (0, 3), (0, 3), (0, 0), 'O'], ['-', (4, 5), (4, 5), (0, 1), 'O'], ['OS', (6, 8), (6, 8), (0, 2), 'O'], ['Intravitreal', (9, 21), (9, 21), (0, 3), 'O'], ['Injection', (22, 31), (22, 31), (0, 4), 'O'], [',', (31, 32), (32, 33), (0, 5), 'O'], ['Pharmacologic', (33, 46), (34, 47), (0, 6), 'O'], ['Agent', (47, 52), (48, 53), (0, 7), 'O'], ['Intravitreal', (57, 69), (54, 66), (0, 8), 'O'], ['Injection', (70, 79), (67, 76), (0, 9), 'O'], ['Procedure', (80, 89), (77, 86), (0, 10), 'O'], ['Note', (90, 94), (87, 91), (0, 11), 'O'], ['Eye', (96, 99), (92, 95), (0, 12), 'O'], [':', (99, 100), (96, 97), (0, 13), 'O'], ['OS', (101, 103), (98, 100), (0, 14), 'O'], ['Pre', (104, 107), (101, 104), (0, 15), 'O'], ['-', (107, 108), (105, 106), (0, 16), 'O'], ['op', (108, 110), (107, 109), (0, 17), 'O'], ['DX', (111, 113), (110, 112), (0, 18), 'O'], [':', (113, 114), (113, 114), (0, 19), 'O'], ['PDR', (114, 117), (115, 118), (0, 20), 'O'], ['Post', (118, 122), (119, 123), (0, 21), 'O'], ['-', (1

2021-06-30 02:23:09,238 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,239 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,240 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_4421.txt ...
2021-06-30 02:23:09,322 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,323 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,323 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_6281.txt ...
2021-06-30 02:23:09,398 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,399 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,399 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_703.txt ...



[[['Visit', (0, 5), (0, 5), (0, 0), 'O'], ['Date', (6, 10), (6, 10), (0, 1), 'O'], [':', (10, 11), (11, 12), (0, 2), 'O'], ['1', (13, 14), (13, 14), (0, 3), 'O'], ['/', (14, 15), (15, 16), (0, 4), 'O'], ['10', (15, 17), (17, 19), (0, 5), 'O'], ['/', (17, 18), (20, 21), (0, 6), 'O'], ['2013', (18, 22), (22, 26), (0, 7), 'O'], ['Referring', (25, 34), (27, 36), (0, 8), 'O'], ['Physician', (35, 44), (37, 46), (0, 9), 'O'], [':', (44, 45), (47, 48), (0, 10), 'O'], ['Dr.', (47, 50), (49, 52), (0, 11), 'O'], ['No', (51, 53), (54, 56), (0, 12), 'O'], ['ref', (54, 57), (57, 60), (0, 13), 'O'], ['.', (57, 58), (61, 62), (0, 14), 'O']], [['provider', (59, 67), (63, 71), (1, 0), 'O'], ['found', (68, 73), (72, 77), (1, 1), 'O'], ['Chief', (75, 80), (78, 83), (1, 2), 'O'], ['Complaint', (81, 90), (84, 93), (1, 3), 'O'], [':', (90, 91), (94, 95), (1, 4), 'O'], ['Chief', (92, 97), (96, 101), (1, 5), 'O'], ['Complaint', (98, 107), (102, 111), (1, 6), 'O'], ['Patient', (109, 116), (112, 119), (1, 7), '

2021-06-30 02:23:09,464 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,465 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,465 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_439.txt ...
2021-06-30 02:23:09,528 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,528 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,529 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_836.txt ...
2021-06-30 02:23:09,590 INFO sentence boundary detection class initiated.
2021-06-30 02:23:09,591 INFO word level tokenization with replace_number set to False
2021-06-30 02:23:09,592 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_169.txt ...
2021-06-30 02:23:09,595 INFO SuperQuad
2021-06-30 02:23:09,596 WARNING 'SuperQuad' => 'Super' 'Quad'
2021-06-30 02:23:09,597 INFO SuperQuad
2021-06-30 02:23:

[[['Assessment', (0, 10), (0, 10), (0, 0), 'O'], ['and', (11, 14), (11, 14), (0, 1), 'O'], ['Plan', (15, 19), (15, 19), (0, 2), 'O'], [':', (19, 20), (20, 21), (0, 3), 'O'], ['ICD', (25, 28), (22, 25), (0, 4), 'O'], ['-', (28, 29), (26, 27), (0, 5), 'O'], ['10', (29, 31), (28, 30), (0, 6), 'O'], ['-', (31, 32), (31, 32), (0, 7), 'O'], ['CM', (32, 34), (33, 35), (0, 8), 'O'], ['ICD', (35, 38), (36, 39), (0, 9), 'O'], ['-', (38, 39), (40, 41), (0, 10), 'O'], ['9', (39, 40), (42, 43), (0, 11), 'O'], ['-', (40, 41), (44, 45), (0, 12), 'O'], ['CM', (41, 43), (46, 48), (0, 13), 'O'], ['1', (46, 47), (49, 50), (0, 14), 'O'], ['.', (47, 48), (51, 52), (0, 15), 'O']], [['Proliferative', (49, 62), (53, 66), (1, 0), 'B-lesion'], ['diabetic', (63, 71), (67, 75), (1, 1), 'I-lesion'], ['retinopathy', (72, 83), (76, 87), (1, 2), 'I-lesion'], ['with', (84, 88), (88, 92), (1, 3), 'O'], ['macular', (89, 96), (93, 100), (1, 4), 'B-lesion'], ['edema', (97, 102), (101, 106), (1, 5), 'I-lesion'], ['associat

In [14]:
# check how many data generated
for k, v in dpos.items():
    print(k, len(v))
    
for k, v in dneg.items():
    print(k, len(v))

0 1548
1 2
0 4150
1 3080


In [15]:
# check data
dpos[1], dneg[1]

([(1,
   'laterality-lesion',
   'Other testing : OCT - Macula : Dme [s1] OU [e1] Assessment Assessment and Plan : 1 .',
   '[s2] Proliferative diabetic retinopathy [e2] ( 362.02 ) 2 .',
   'laterality',
   'lesion',
   'T9',
   'T3',
   'note_4453'),
  (1,
   'laterality-lesion',
   'OCT , Posterior Segment - OU - Both Eyes OD : Drusen , no SRF [s1] OS [e1] : Geo atrophy , Drusen .',
   'No [s2] SRF [e2] Assessment and Plan : ICD - 10 - CM ICD - 9 - CM 1 .',
   'laterality',
   'lesion',
   'T5',
   'T2',
   'note_1142')],
 [(1,
   'NonRel',
   'POW # ID [s1] OD [e1] from PPV for VH , vitritis , TRD from secondary complications .',
   'Hx of previous [s2] exudative [e2] RD OU .',
   'laterality',
   'lesion',
   'T4',
   'T2',
   '2748168_note_9227'),
  (1,
   'NonRel',
   'Hx of previous exudative RD [s1] OU [e1] .',
   'POW # ID OD from PPV for [s2] VH [e2] , vitritis , TRD from secondary complications .',
   'laterality',
   'lesion',
   'T5',
   'T1',
   '2748168_note_9227'),
  (1

In [28]:
# output data
all_in_one(dpos, dneg, dn="dr", do_train=True)
all_in_unique(dpos, dneg, dn="dr", do_train=True)

In [26]:
output_path

NameError: name 'output_path' is not defined

## Generate test data

In [17]:
preds = create_test_samples(test_root, None, dr_valid_comb_en)

2021-06-30 02:26:05,768 INFO sentence boundary detection class initiated.
2021-06-30 02:26:05,769 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:05,770 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7357.txt ...
2021-06-30 02:26:05,833 INFO sentence boundary detection class initiated.
2021-06-30 02:26:05,834 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:05,848 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/876827_note_1263.txt ...
2021-06-30 02:26:05,917 INFO sentence boundary detection class initiated.
2021-06-30 02:26:05,918 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:05,918 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_439.txt ...
2021-06-30 02:26:05,981 INFO sentence boundary detection class initiated.
2021-06-30 02:26:05,982 INFO word level tokenization with replace_number set 

first index not match  ('eft eye', 'laterality', (560, 567))


2021-06-30 02:26:06,520 INFO sentence boundary detection class initiated.
2021-06-30 02:26:06,521 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:06,521 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_702.txt ...
2021-06-30 02:26:06,590 INFO sentence boundary detection class initiated.
2021-06-30 02:26:06,591 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:06,592 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/2678512_note_8911.txt ...
2021-06-30 02:26:06,652 INFO sentence boundary detection class initiated.
2021-06-30 02:26:06,653 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:06,653 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_4045.txt ...
2021-06-30 02:26:06,715 INFO sentence boundary detection class initiated.
2021-06-30 02:26:06,716 INFO word level tokenization with replace_number set

2021-06-30 02:26:08,511 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:08,511 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1145464_note_2230.txt ...
2021-06-30 02:26:08,605 INFO sentence boundary detection class initiated.
2021-06-30 02:26:08,606 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:08,607 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_169.txt ...
2021-06-30 02:26:08,611 INFO SuperQuad
2021-06-30 02:26:08,611 WARNING 'SuperQuad' => 'Super' 'Quad'
2021-06-30 02:26:08,613 INFO SuperQuad
2021-06-30 02:26:08,613 WARNING 'SuperQuad' => 'Super' 'Quad'
2021-06-30 02:26:08,684 INFO sentence boundary detection class initiated.
2021-06-30 02:26:08,685 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:08,686 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_703.txt ...
2021-06-30 02:26:08,748

last index not match  ('MA', 'lesion', (699, 701))
last index not match  ('MA', 'lesion', (868, 870))


...

2021-06-30 02:26:12,894 INFO sentence boundary detection class initiated.
2021-06-30 02:26:12,894 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:12,895 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_2162.txt ...
2021-06-30 02:26:12,974 INFO sentence boundary detection class initiated.
2021-06-30 02:26:12,975 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:12,976 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_1533.txt ...
2021-06-30 02:26:13,035 INFO sentence boundary detection class initiated.
2021-06-30 02:26:13,036 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:13,036 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_8850.txt ...
2021-06-30 02:26:13,098 INFO sentence boundary detection class initiated.
2021-06-30 02:26:13,099 INFO word level tokenization with replace_number set to Fal

last index not match  ('Right', 'laterality', (1346, 1353))
last index not match  ('Left', 'laterality', (2351, 2357))


2021-06-30 02:26:14,701 INFO sentence boundary detection class initiated.
2021-06-30 02:26:14,701 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:14,702 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_2444.txt ...
2021-06-30 02:26:14,706 WARNING '7.2 ' cannot be parsed by current rule.
2021-06-30 02:26:14,767 INFO sentence boundary detection class initiated.
2021-06-30 02:26:14,768 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:14,769 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1424866_note_3176.txt ...
2021-06-30 02:26:14,827 INFO sentence boundary detection class initiated.
2021-06-30 02:26:14,828 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:14,829 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1936668_note_5255.txt ...
2021-06-30 02:26:14,894 INFO sentence boundary detection class initi

last index not match  ('severe', 'severity', (1734, 1741))
last index not match  ('OD', 'laterality', (1987, 1990))
last index not match  ('OS', 'laterality', (2032, 2035))
last index not match  ('MA', 'lesion', (450, 452))


2021-06-30 02:26:15,461 INFO sentence boundary detection class initiated.
2021-06-30 02:26:15,462 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:15,462 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/2476700_note_7181.txt ...
2021-06-30 02:26:15,523 INFO sentence boundary detection class initiated.
2021-06-30 02:26:15,524 INFO word level tokenization with replace_number set to False
2021-06-30 02:26:15,525 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_3956.txt ...


In [18]:
for k, v in preds.items():
    print(k, len(v))

0 2426
1 1278


In [19]:
preds[1]

[(1,
  'NonRel',
  'Treatment Hx IVFA - PRP and focal laser scars with [s1] active [e1] NVE OU .',
  'Diabetes mellitus due to underlying condition with chronic kidney disease on chronic dialysis , with long - term current use of insulin E08 . 22 249.40 N18.6 585.9 Z79.4 V45.11 Z99.2 V58.67 Mr. Caine is a 72 year old male with a h / o PDR OU s / p PRP OU Referred from Dr. Grieser for evaluation of possible [s2] NVE [e2] seen clinically .',
  'severity',
  'lesion',
  'T9',
  'T3',
  'note_439'),
 (1,
  'NonRel',
  'Treatment Hx IVFA - PRP and focal laser scars with [s1] active [e1] NVE OU .',
  'Diabetes mellitus due to underlying condition with chronic kidney disease on chronic dialysis , with long - term current use of insulin E08 . 22 249.40 N18.6 585.9 Z79.4 V45.11 Z99.2 V58.67 Mr. Caine is a 72 year old male with a h / o [s2] PDR [e2] OU s / p PRP OU Referred from Dr. Grieser for evaluation of possible NVE seen clinically .',
  'severity',
  'lesion',
  'T9',
  'T18',
  'note_439'

In [24]:
all_in_one(preds, dn="dr", do_train=False)

In [25]:
all_in_unique(preds, dn="dr", do_train=False)

In [14]:
# create ann for test purpose
def extract_only_entity(input_path, output_path):
    pi = Path(input_path)
    po = Path(output_path)
    po.mkdir(exist_ok=True, parents=True)
    for fid in pi.glob("*.ann"):
        ofn = po / fid.name
        with open(fid, "r") as f1, open(ofn, "w") as f2:
            for line in f1.readlines():
                if line.startswith("T"):
                    f2.write(line)

In [30]:
test_root_output = '/home/zehao.yu/workspace/py3/dr_ann/data/data_annotation_entity_only'
extract_only_entity(test_root, test_root_output)

# create test data end 2 end

In [11]:
preds = create_test_samples(test_root_e2e, None, dr_valid_comb_en)


2021-07-01 18:39:11,149 INFO sentence boundary detection class initiated.
2021-07-01 18:39:11,149 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:11,150 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_7357.txt ...
2021-07-01 18:39:11,257 INFO sentence boundary detection class initiated.
2021-07-01 18:39:11,257 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:11,258 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/876827_note_1263.txt ...
2021-07-01 18:39:11,392 INFO sentence boundary detection class initiated.
2021-07-01 18:39:11,393 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:11,393 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_439.txt ...
2021-07-01 18:39:11,453 INFO sentence boundary detection class initiated.
2021-07-

2021-07-01 18:39:13,140 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:13,141 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_6281.txt ...
2021-07-01 18:39:13,208 INFO sentence boundary detection class initiated.
2021-07-01 18:39:13,209 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:13,210 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/2542462_note_7938.txt ...
2021-07-01 18:39:13,212 INFO SuperQuad
2021-07-01 18:39:13,213 WARNING 'SuperQuad' => 'Super' 'Quad'
2021-07-01 18:39:13,314 INFO sentence boundary detection class initiated.
2021-07-01 18:39:13,315 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:13,316 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_487.txt ...
2021-07-01 18:39:13,371 INFO sentence boundary detecti

2021-07-01 18:39:14,892 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:14,893 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/1036182_note_1786.txt ...
2021-07-01 18:39:14,952 INFO sentence boundary detection class initiated.
2021-07-01 18:39:14,953 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:14,954 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_7843.txt ...
2021-07-01 18:39:15,027 INFO sentence boundary detection class initiated.
2021-07-01 18:39:15,028 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:15,028 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_4013.txt ...
2021-07-01 18:39:15,083 INFO sentence boundary detection class initiated.
2021-07-01 18:39:15,084 INFO word level tokenization with replace_number set to 

2021-07-01 18:39:16,677 INFO sentence boundary detection class initiated.
2021-07-01 18:39:16,678 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:16,679 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/1230653_note_2636.txt ...
2021-07-01 18:39:16,733 INFO sentence boundary detection class initiated.
2021-07-01 18:39:16,734 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:16,735 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_9154.txt ...
2021-07-01 18:39:16,798 INFO sentence boundary detection class initiated.
2021-07-01 18:39:16,799 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:16,800 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_5885.txt ...
2021-07-01 18:39:16,871 INFO sentence boundary detection class initiated.
2021-0

2021-07-01 18:39:18,329 WARNING 'LORazepam' => 'LO' 'Razepam'
2021-07-01 18:39:18,425 INFO sentence boundary detection class initiated.
2021-07-01 18:39:18,426 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:18,427 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_7667.txt ...
2021-07-01 18:39:18,485 INFO sentence boundary detection class initiated.
2021-07-01 18:39:18,486 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:18,487 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_2162.txt ...
2021-07-01 18:39:18,577 INFO sentence boundary detection class initiated.
2021-07-01 18:39:18,578 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:18,578 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_1533.txt ...
2021-07-01 18:39:18,632 IN

2021-07-01 18:39:20,264 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_4017.txt ...
2021-07-01 18:39:20,338 INFO sentence boundary detection class initiated.
2021-07-01 18:39:20,338 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:20,339 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/note_2444.txt ...
2021-07-01 18:39:20,343 WARNING '7.2 ' cannot be parsed by current rule.
2021-07-01 18:39:20,400 INFO sentence boundary detection class initiated.
2021-07-01 18:39:20,401 INFO word level tokenization with replace_number set to False
2021-07-01 18:39:20,402 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/result/bert_mimic_result_formatted_output/1424866_note_3176.txt ...
2021-07-01 18:39:20,465 INFO sentence boundary detection class initiated.
2021-07-01 18:39:20,466 INFO word level tokenization with replace_number set to False
2021-07

In [12]:
for k, v in preds.items():
    print(k, len(v))

0 2505
1 1339


In [17]:
all_in_one(preds, dn="dr_etoe", do_train=False)

In [16]:
test_root_output_e2e = '/home/zehao.yu/workspace/py3/dr_ann/data/data_annotation_entity_only_etoe'
extract_only_entity(test_root_e2e, test_root_output_e2e)

In [ ]:
#evaulation

In [20]:
! python brat_eval.py --f1 ../data/used/test_set --f2 ../result/relation_predicted_results_bert

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Eye_part  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Severity  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
          Laterality  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
                      ------------------------------------------------
     Overall (micro)  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
     Overall (macro)  0.9448  0.9448  0.9448    0.9448  0.9448  0.9448

***************************** RELATIONS ******************************
             located  1.0000  0.8571  0.9231    1.0000  0.8571  0.9231
     severity-lesion  0.9454  0.9454  0.9454    0.9454  0.9454  0.9454
   laterality-lesion  0.9081  0.9457  0.9265    0.9081  0.9457  0.9265
     

In [19]:
! python brat_eval.py --f1 ../data/used/test_set --f2 ../result/relation_predicted_results_bert_e2e

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9555  0.9576  0.9565    0.9776  0.9743  0.9760
            Eye_part  0.8000  0.7059  0.7500    0.8000  0.7059  0.7500
            Severity  0.9627  0.9317  0.9469    0.9668  0.9357  0.9510
          Laterality  0.9339  0.9608  0.9472    0.9439  0.9711  0.9573
                      ------------------------------------------------
     Overall (micro)  0.9486  0.9520  0.9503    0.9642  0.9648  0.9645
     Overall (macro)  0.8908  0.8838  0.8836    0.9125  0.9062  0.9056

***************************** RELATIONS ******************************
             located  0.7692  0.7143  0.7407    0.7692  0.7143  0.7407
     severity-lesion  0.9162  0.8962  0.9061    0.9218  0.9016  0.9116
   laterality-lesion  0.8138  0.8739  0.8428    0.8554  0.9130  0.8833
     

In [23]:
! python brat_eval.py --f1 ../data/used/test_set --f2 ../result/relation_predicted_results_roberta

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Eye_part  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Severity  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
          Laterality  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
                      ------------------------------------------------
     Overall (micro)  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
     Overall (macro)  0.9448  0.9448  0.9448    0.9448  0.9448  0.9448

***************************** RELATIONS ******************************
             located  1.0000  0.8571  0.9231    1.0000  0.8571  0.9231
     severity-lesion  0.9312  0.9617  0.9462    0.9312  0.9617  0.9462
   laterality-lesion  0.8891  0.9587  0.9226    0.8891  0.9587  0.9226
     

In [24]:
! python brat_eval.py --f1 ../data/used/test_set --f2 ../result/relation_predicted_results_roberta_e2e


******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9555  0.9576  0.9565    0.9776  0.9743  0.9760
            Eye_part  0.8000  0.7059  0.7500    0.8000  0.7059  0.7500
            Severity  0.9627  0.9317  0.9469    0.9668  0.9357  0.9510
          Laterality  0.9339  0.9608  0.9472    0.9439  0.9711  0.9573
                      ------------------------------------------------
     Overall (micro)  0.9486  0.9520  0.9503    0.9642  0.9648  0.9645
     Overall (macro)  0.8908  0.8838  0.8836    0.9125  0.9062  0.9056

***************************** RELATIONS ******************************
             located  0.8333  0.7143  0.7692    0.8333  0.7143  0.7692
     severity-lesion  0.9176  0.9126  0.9151    0.9231  0.9180  0.9205
   laterality-lesion  0.7953  0.8870  0.8386    0.8333  0.9239  0.8763
     

In [ ]:
! python brat_eval.py --f1 ../data/used/test_set --f2 ../result/relation_predicted_results_roberta_e2e